Maxwell Equations - Time harmonic low frequency
===

In [1]:
from netgen.csg import *
from ngsolve import *
from ngsolve.webgui import Draw

Geometric model using Netgen constructive solid geometry:

In [2]:
def MakeGeometry():
    geometry = CSGeometry()
    box = OrthoBrick(Pnt(-2,-2,-2),Pnt(2,2,2)).bc("outer")

    plate = OrthoBrick(Pnt(-0.8,-0.8,0.9),Pnt(0.8,0.8,1)).maxh(0.1).mat("plate")
    
    coil = (Cylinder(Pnt(0.05,0,0), Pnt(0.05,0,0.4), 0.3) - \
            Cylinder(Pnt(0.05,0,0), Pnt(0.05,0,0.4), 0.15)) * \
            OrthoBrick (Pnt(-1,-1,0.3),Pnt(1,1,0.4)).maxh(0.1).mat("coil")
    
    geometry.Add ((box-plate-coil).mat("air"), transparent=True)
    geometry.Add (plate)
    geometry.Add (coil)
    return geometry

geo = MakeGeometry()
# Draw (geo)

In [3]:
mesh = Mesh(geo.GenerateMesh(maxh=0.5))
mesh.Curve(5)
Draw (mesh, clipping = { "pnt" : (0,0,0), "vec" : (0,1,0) })

WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.24…

BaseWebGuiScene

Harmonics low frequency Maxwell's:


find $u \in H(curl)$ such that
$$
\int i \omega\sigma uv + \int \mu^{-1} \operatorname{curl} u \operatorname{curl} v = \int j v
$$
for all $v \in H(curl)$.

In [7]:
fes = HCurl(mesh, order = 3, dirichlet="outer", nograds = False, complex = True)
print ("ndof =", fes.ndof)
u,v = fes.TnT()

import math
omega = 2*math.pi*50
mur = { "plate" : 1, "coil" : 1, "air" : 1 }
sigma = {"plate": 1e7, "coil": 1, "air": 0}
mu0 = 1.257e-6
nu_coef = [ 1/(mu0*mur[mat]) for mat in mesh.GetMaterials() ]
eta_coef = [ 1j*omega*sigma[mat] for mat in mesh.GetMaterials() ]

nu = CoefficientFunction(nu_coef)
eta = CoefficientFunction(eta_coef)
a = BilinearForm(fes, symmetric=False)
a += eta*u*v*dx + nu*curl(u)*curl(v)*dx + 1e-6*nu*u*v*dx

c = Preconditioner(a, type="bddc")

f = LinearForm(fes)
f += CoefficientFunction((y,0.05-x,0)) * v * dx("coil")

u = GridFunction(fes)

ndof = 526540


Distribute work by task-parallelization:

In [8]:
with TaskManager():
    a.Assemble()
    f.Assemble()
    solver = CGSolver(mat=a.mat, pre=c.mat)
    u.vec.data = solver * f.vec
    #u.vec.data = a.mat.Inverse(freedofs=fes.FreeDofs()) * f.vec
   

In [9]:
Draw (curl(u), mesh, "B-field", draw_surf=False, \
      clipping = { "pnt" : (0,0,0), "vec" : (0,1,0), "function" : False },
      vectors = { "grid_size" : 100 })

WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.24…

BaseWebGuiScene